# Lab Work 1: Working with missing data
This excercise should give you some practice in working with missing data of different feature types.

**Please note, that you can only pass the intial checking, if you write Markdown documention about your findings (not code documentation). Any submission that does not adhere to that will lead to an immediate fail, without the chance of resubmission!**

# 1. Load the iris dataset with missing values into a dataframe 
File: datasets.zip/datasets/iris/data_someMissing.all

Hint: When data is missing, pandas might not be able to determine the proper type of columns by itself. Look carefully at the data types and act accordingly! You have different options to change the types of columns:
* When reading, have a look at [pandas.read_csv](https://pandas.pydata.org/docs/reference/api/pandas.read_csv.html), esp the parameter *na_filter*
* In memory, have a look at [dataframe.astype](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.astype.html) and the transformation functions [dataframe.apply](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.apply.html) in combination with [pandas.to_numeric](https://pandas.pydata.org/docs/reference/api/pandas.to_numeric.html)

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns


my_dataframe = pd.read_csv('datasets/iris/data_someMissing.all', 
                        sep=' ', 
                        na_values=['?'],
                        header=None,
                        names=['sl', 'sw', 'pl', 'pw', 'class'])

print("Datentypen nach dem Einlesen:")
print(my_dataframe.dtypes)


# Verwende hier den zweiten Ansatz mit dataframe.apply und pandas.to_numeric, da diese robuster und flexibler ist als dataframe.astype
numeric_cols = ['sl', 'sw', 'pl', 'pw']
my_dataframe[numeric_cols] = my_dataframe[numeric_cols].apply(pd.to_numeric, errors='coerce')

print("\nDatentypen nach apply(pd.to_numeric):")
print(my_dataframe.dtypes)

my_dataframe

# 2. What are your options to work with the missing values? 
- Löschen (Deletion)
    - Listwise Deletion: Entferne alle Zeilen mit fehlenden Werten
- Imputation mit statistischen Werten
    - Mean Imputation: Ersetze durch Mittelwert der ganzen Spalte
    - Median Imputation: Ersetze durch Median der ganzen Spalte (robuster gegen Ausreißer)
    - Class-spezifische Imputation: Ersetze durch Mittelwert/Median der Spalte gefilter nach jeweiligen Klasse
- Markierung
    - Fehlende Werte als separate Kategorie behandeln

# 3. What is their difference with respect to the features of the dataset and the class associations? 
- Auswirkungen auf Features:
    - Mean Imputation verändert nicht den Mittelwert, reduziert aber die Varianz​
    - Median Imputation ist robuster bei schiefen Verteilungen​
    - (Listwise) Deletion reduziert die Datenmenge und kann daher zu Bias führen, wenn unverhältnismäßig viel aus einer Klasse gelöscht wird

- Auswirkungen auf Klassenzugehörigkeit
    - Mean/ Median Imputation können die klassenspezifischen Muster durch das einsetzten global ermittelter Werte verzerren
    - Class-spezifische Imputation erhält hingegen klassenspezifische Muster besser bei
    - Deletion kann Klassenverteilung verändern, wenn fehlende Werte nicht zufällig verteilt sind

# 4. Implement some of the options for the dataset
* check, how these options change the statistical values of
  * each feature
  * each class
* Visualize and Interpret your results
  * you can use a visualization framework of your choice
  * you MUST write Markdown documentation of your findings!
* useful functions in pandas for this step
  * find out, if a value [is null](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.isnull.html)
  * [removing data that null ](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.dropna.html?highlight=dropna)
  * [fill null data with other value](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.fillna.html)
  * [replace values](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.replace.html)

## 4.1 Implentierung der Optionen

In [ ]:
numeric_cols = ['sl', 'sw', 'pl', 'pw']

# Original Daten
df_original = my_dataframe.copy()

# Strategie 1: Listwise Deletion
df_deletion = my_dataframe.copy().dropna()

# Strategie 2: Mean Imputation (global)
df_mean = my_dataframe.copy()
for col in numeric_cols:
    df_mean[col].fillna(df_mean[col].mean(), inplace=True)

# Strategie 3: Median Imputation (global)
df_median = my_dataframe.copy()
for col in numeric_cols:
    df_median[col].fillna(df_median[col].median(), inplace=True)

# Strategie 4: Class-spezifische Mean Imputation
df_class_mean = my_dataframe.copy()
for class_name in df_class_mean['class'].dropna().unique():
    class_mask = df_class_mean['class'] == class_name
    for col in numeric_cols:
        class_mean = df_class_mean.loc[class_mask, col].mean()
        df_class_mean.loc[class_mask, col] = df_class_mean.loc[class_mask, col].fillna(class_mean)
df_class_mean = df_class_mean.dropna(subset=['class']) # Fehlende Klassenlabels separat behandeln


## 4.2 Statistische Auswertung
### 4.2.1 Implementierung der statistische Auswertung

In [ ]:
# Funktion für statistische Zusammenfassung
def print_statistics(df, name, df_original=None):
    print(f"\n{'='*50}")
    print(f"Statistiken für: {name}")
    print(f"{'='*50}")
    print(f"Anzahl Datenpunkte: {len(df)} ", end='')
    
    if df_original is not None:
        diff_count = len(df) - len(df_original)
        print(f"(Δ: {diff_count:+d})")
    else:
        print()
    
    if df_original is not None:
        print(f"\nDeskriptive Statistik mit Abweichungen zum Original:")
        
        stats_current = df.describe()
        stats_original = df_original.describe()
        
        # Interleaved Format: Wert | Abweichung für jede Spalte
        result_dict = {}
        
        for col in stats_current.columns:
            if col in stats_original.columns:
                result_dict[f'{col}_cur'] = stats_current[col]
                result_dict[f'{col}_Δ'] = stats_current[col] - stats_original[col]
        
        result_df = pd.DataFrame(result_dict)
        
        # Sortiere Spalten so, dass sie paarweise erscheinen
        sorted_cols = []
        base_cols = [c.replace('_cur', '').replace('_Δ', '') 
                     for c in result_df.columns if '_cur' in c]
        for base in base_cols:
            sorted_cols.extend([f'{base}_cur', f'{base}_Δ'])
        
        print(result_df[sorted_cols].to_string(float_format=lambda x: f'{x:8.8f}'))
    else:
        print(f"\nDeskriptive Statistik:")
        print(df.describe())
    
    print(f"\nKlassenverteilung:")
    class_counts = df['class'].value_counts()
    
    if df_original is not None:
        original_counts = df_original['class'].value_counts()
        # DataFrame mit Aktuell und Abweichung
        class_comparison = pd.DataFrame({
            'Aktuell': class_counts,
            'Δ': class_counts - original_counts
        })
        print(class_comparison)
    else:
        print(class_counts)


### 4.2.2 Ausgabe der statistische Auswertung

In [ ]:
print_statistics(df_original, "Original (mit fehlenden Werten)", df_original)

In [ ]:
print_statistics(df_deletion, "Listwise Deletion", df_original)

In [ ]:
print_statistics(df_mean, "Mean Imputation", df_original)

In [ ]:
print_statistics(df_median, "Median Imputation", df_original)

In [ ]:
print_statistics(df_class_mean, "Class-spezifische Mean Imputation", df_original)

#### 4.2.2.1 Auswertung der Ausgaben/ Ergebnisse
##### a) Listwise Deletion
- Es kommt zu einem beträchtlichen Datenverlust durch die Reduktion von 150 auf 145 Datenpunkte (3,3% Verlust)
- Die fehlenden Werte konzentrieren sich auf Iris-setosa, was auf einen systematischen Bias hindeutet. Die gelöschten Setosa-Exemplare hatten unterdurchschnittliche pl
Werte, wodurch der Gesamtmittelwert künstlich steigt. Dies führt zudem zu einer verzerrten Klassenverteilung (50, 50, 45).
- Die Mittelwerte verschieben sich, was auf eine nicht-zufällige Verteilung der fehlenden Werte hindeutet

|      | sl_cur     | sl_Δ       | sw_cur     | sw_Δ        | pl_cur     | pl_Δ       | pw_cur     | pw_Δ       |
|------|------------|------------|------------|-------------|------------|------------|------------|------------|
| mean | 5.87034483 | 0.02604953 | 3.04344828 | -0.00890072 | 3.84000000 | 0.06617450 | 1.23379310 | 0.02027959 |

**Fazit:**
Modelle werden auf unbalancierten Daten (45:50:50) trainiert. Dies führt zu schlechterer Vorhersagegenauigkeit für Iris-setosa, da weniger Trainingsbeispiele verfügbar sind. Wegen der ungleichmäßigen Klassenverteilung und der Veränderung der Mittelwerte wird *Listwise Deletion* nicht empfohlen

##### b) Mean Imputation (global)
Verbesserungen zur Listwise Deletion
- Mittelwerte bleiben identisch zum Original

|      | sl_cur     | sl_Δ        | sw_cur     | sw_Δ        | pl_cur     | pl_Δ       | pw_cur     | pw_Δ       |
|------|------------|-------------|------------|-------------|------------|------------|------------|------------|
| mean | 5.84429530 | -0.00000000 | 3.05234899 | -0.00000000 | 3.77382550 | 0.00000000 | 1.21351351 | 0.00000000 |

- Alle 150 Datenpunkte bleiben erhalten (minus 1 ohne Klassenlabel), wodurch die Klassenverteilung ausgeglichen bleibt (50, 50, 49).

weiterhin problematisch
- die Standardabweichung sinkt bei allen Features im Vergleich zum Original, was eine künstlichen vereinheitlichung der Datenverteilung und Varianzreduktion zur Folge hat

|     | sl_cur     | sl_Δ        | sw_cur     | sw_Δ        | pl_cur     | pl_Δ        | pw_cur     | pw_Δ        |
|-----|------------|-------------|------------|-------------|------------|-------------|------------|-------------|
| std | 0.82798231 | -0.00279253 | 0.43157024 | -0.00145555 | 1.75462556 | -0.00591781 | 0.75232513 | -0.00510057 |

- Es wird ein globaler Mittelwert über alle Klassen hinweg verwendet. Die klassenspezifische Unterschiede verwischen dadurch.
    - Beispiel: Fehlende pl Werte bei Iris-setosa (ca. 1,4 cm) werden durch den globalen Mittelwert (ca. 3.8 cm) ersetzt, was die natürlichen Unterschiede zwischen den Arten reduziert.

##### c) Median Imputation - Ähnlich wie Mean Imputation
- Die Ergebnisse sind nahezu identisch mit Mean Imputation und weisen ähnliche Abweichungen zum Original auf

|      | sl_cur     | sl_Δ        | sw_cur     | sw_Δ        | pl_cur     | pl_Δ        | pw_cur     | pw_Δ        |
|------|------------|-------------|------------|-------------|------------|-------------|------------|-------------|
| mean | 5.84400000 | -0.00029530 | 3.05200000 | -0.00034899 | 3.77800000 | 0.00417450  | 1.21466667 | 0.00115315  |
| std  | 0.82799021 | -0.00278463 | 0.43159141 | -0.00143439 | 1.75537028 | -0.00517309 | 0.75239097 | -0.00503473 |

**Fazit:** Die Median Imputation wäre robuster gegen Ausreißer, die in diesem Datensatz aber nicht vorhanden sind. Somit ergeben sich keine merklichen Vorteile zur Mean Imputation.


##### d) Class-spezifische Mean Imputation
Verbesserungen zu den Imputations
- geringste Abweichung der Standardabweichungen zum Original

| Statistik     | sl_cur     | sl_Δ        | sw_cur     | sw_Δ        | pl_cur     | pl_Δ        | pw_cur     | pw_Δ        |
|---------------|------------|-------------|------------|-------------|------------|-------------|------------|-------------|
| std_csMeanImp | 0.83009005 | -0.00068478 | 0.43409672 | +0.00107093 | 1.76087327 | +0.00032990 | 0.75754371 | +0.00011800 |
| std_del       | 0.82167885 | -0.00909599 | 0.43073158 | -0.00229421 | 1.73775078 | -0.02279259 | 0.75168521 | -0.00574049 |
| std_meanImp   | 0.82798231 | -0.00279253 | 0.43157024 | -0.00145555 | 1.75462556 | -0.00591781 | 0.75232513 | -0.00510057 |
| std_medImp    | 0.82799021 | -0.00278463 | 0.43159141 | -0.00143439 | 1.75537028 | -0.00517309 | 0.75239097 | -0.00503473 |

- Es werden die Mittelwerte der jeweiligen Klasse verwendet und keinen globalen Mittelwert wie bei Mean und Median Imp. Die Unterschiede zwischen den Klassen verwischen dadurch nicht.
- Ausgeglichene Klassenverteilung: 50, 50, 49 (nur 1 Datenpunkt mit fehlendem Klassenlabel entfernt)

### 4.2.3 Vergleich der globalen und klassenspezifischen Mittelwerte

In [ ]:
# Klassenspezifische Mittelwerte vergleichen
print("Mittelwerte pro Klasse - Class-Mean Imputation:")
print(df_class_mean.groupby('class')[numeric_cols].mean())

In [ ]:
print("\nMittelwerte pro Klasse - Global Mean Imputation:")
print(df_mean.groupby('class')[numeric_cols].mean())

In [ ]:
print("\nAbweichung Class-Mean vs. Global Mean:")
class_diff = df_class_mean.groupby('class')[numeric_cols].mean() - df_mean.groupby('class')[numeric_cols].mean()
print(class_diff)


##### 4.2.3.1 Auswertung des Vergleichs der globalen und klassenspezifischen Mittelwerte
Bei Global Mean Imputation erhalten alle Klassen die gleichen Ersatzwerte (globaler Mittelwert), was besonders bei Iris-setosa problematisch ist. Die Abweichungstabelle zeigt, dass Setosa-Werte durch zu große pl/ pw Ersatzwerte verfälscht werden.

Wenn ein Setosa-Exemplar einen fehlenden pl Wert hat, wird bei 
- Global Mean durch ca. 3.7 cm ersetzt, was sehr stark von anderen Werten aus der Klasse abweicht,
- Class-Mean durch ca. 1.4 cm ersetzt, was eher den vorhandenen Eigenschaften der Klasse passt

**Fazit:**
Class-spezifische Imputation bewahrt die Unterschiede zwischen den Arten und verhindert, dass z.B. Setosa-Exemplare künstlich andere Merkmale erhalten. 

### 4.2.4 Visualisierung der statistische Auswertung

In [ ]:
fig, axes = plt.subplots(2, 2, figsize=(15, 10))
features = ['sl', 'sw', 'pl', 'pw']

for idx, feature in enumerate(features):
    ax = axes[idx//2, idx%2]

    # Boxplots für verschiedene Strategien
    data_to_plot = [
        df_deletion[feature],
        df_mean[feature],
        df_median[feature],
        df_class_mean[feature]
    ]

    ax.boxplot(data_to_plot, tick_labels=['Deletion', 'Mean', 'Median', 'Class-Mean'])
    ax.set_title(f'{feature}')
    ax.set_ylabel('Wert')
    ax.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

print("Tabelle: Vergleich der Mittelwerte und Standardabweichungen")
comparison_data = []
for strategy_name, df_strategy in [('Original', df_original),
                                    ('Deletion', df_deletion),
                                    ('Mean', df_mean),
                                    ('Median', df_median),
                                    ('Class-Mean', df_class_mean)]:
    for feature in features:
        comparison_data.append({
            'Feature': feature,
            'Strategie': strategy_name,
            'Mittelwert': df_strategy[feature].mean(),
            'Std': df_strategy[feature].std()
        })

df_comparison = pd.DataFrame(comparison_data)
df_comparison


#### 4.2.4.1 Auswertung der Visualsierung
##### Boxplot-Analyse
Die Boxplots zeigen deutliche Unterschiede zwischen den Strategien:
- **sl & sw:** Alle Strategien produzieren nahezu identische Verteilungen (Median und Quartile überlagern sich), da hier wenige fehlende Werte vorlagen.
- **pl:** Listwise Deletion verschiebt den Median leicht nach oben (sichtbar in der Box-Position), was die Löschung kleinerer Setosa-Werte bestätigt. Die Imputation-Strategien erhalten die Median-Position besser.
- **pw:** Ähnliches Muster wie pl, aber weniger ausgeprägt.

##### Vergleichstabelle-Analyse
Die df_comparison Tabelle zeigt, dass Class-Mean Imputation die geringsten Abweichungen bei den Standardabweichungen aufweist, während andere Methoden durchweg Varianzreduktion zeigen.

##### Fazit
Visuell sind die Unterschiede minimal, aber statistisch relevant. Die Erhaltung der Variabilität (Box-Höhe) ist bei Class-Mean am besten, was für robuste nachfolgende Analysen sorgen wird.


## 5. Abschlißende Empfehlung
Class-spezifische Mean Imputation
- Die Standardabweichung bleibt am nächsten zum Original. Diese bessere Erhaltung der Streuung bildet die natürliche Variabilität biologischer Messungen besser ab.
- Die Ersetzung der fehlenden Werte durch klassenspezifische Mittelwerte anstelle der globalen Mittelwerte verhindert, dass zB Iris-Setosa "Ausreißer" in pw bekommen und somit die Eigenschaften der Klassen verwischen.
- Bei der class-spezifischen Mean Imputation geht nur ein einziger Datenpunkt verloren. Der Datensatz mit fehlendem Klassenlabel (Zeile 10), da hier keine Klassenzugehörigkeit für die Imputation ermittelt werden kann. Die Klassenverteilung bleibt daher ausgeglichener (49:50:50). Dies vermeidet eine Verzerrung, der bei Listwise Deletion entsteht (45:50:50) und bei nachfolgenden Klassifikationsaufgaben zu einer Benachteiligung der Iris-setosa Klasse führen würde.